In [6]:
import numpy as np
import itertools
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import scipy as sp
import time

# import functions for ODE parameter estimation
from model.diag_Gaussian import *

np.random.seed(123)

## Define ODE (x, time, parameters)

In [2]:
# ode 
def system(x, t, params): 

    # unpack parameters
    mu_max, pref, alpha, K_inv, delta = params
    
    # unpack variables
    od, pH = x 
    
    # coupled ODE for cells and environmental pH
    dod = od * (mu_max - K_inv * od) * (jnp.exp(-alpha * (pH - pref)**2) - delta)
    dpH = 0. 
    
    return jnp.array([dod, dpH])  

# define transform function to constrain parameter values
def transform(params):

    # unpack parameters
    mu_max, pref, alpha, K_inv, delta = params
    
    # take exp of strictly positive parameters
    mu_max = jnp.exp2(mu_max)
    pref = 7.*jnp.exp2(pref)
    alpha = jnp.exp2(alpha)/100.
    K_inv = jnp.exp2(K_inv)/10.
    delta = jnp.exp2(delta)/10.
    
    return jnp.array([mu_max, pref, alpha, K_inv, delta])

# define prior mean of transformed variables 
prior_mean = jnp.array([1., 7., 0., 1., 0.])

# prior precision 
alpha = 10. 

## Import data as a Pandas dataframe 

The dataframe must have a "Treatments" column that provides a unique identifier for each condition. The second column specifies the time point that observations were made. The following columns include the state variables.

In [3]:
# import data
df = pd.read_csv("Data/arc_allmono.csv").rename(columns={"Experiments":"Treatments"})

In [4]:
# species names
all_species = df.columns.values[3:]
all_species

array(['AC_OD', 'BA_OD', 'BC_OD', 'BL_OD', 'BT_OD', 'BV_OD', 'CC_OD',
       'DF_OD', 'wt_OD', 'delarc_OD', 'parc-_OD', 'parc+_OD'],
      dtype=object)

In [5]:
# loop over monocultures
for sp in all_species:
    
    # init list of dataframes of model predictions
    df_preds = []

    # pH vals
    ph_vals = [4, 5, 6, 7, 8, 9]
    
    # loop over ph values
    for ph_val in ph_vals:
    
        # names of species in ODE
        species = [sp, 'pH']
    
        # pull out train and test dataframes
        df_train = pd.concat([df_exp for exp_name, df_exp in df.groupby("Treatments") if sp.split("_")[0] in exp_name and str(ph_val) not in exp_name])
        df_test  = pd.concat([df_exp for exp_name, df_exp in df.groupby("Treatments") if sp.split("_")[0] in exp_name and str(ph_val) in exp_name])
        
        # average test data over time
        df_groups = df_test.groupby("Time")
        df_test = df_groups[species].mean().reset_index()
        df_test.insert(0, "Treatments", [sp.split("_")[0]+"_"+str(ph_val)]*df_test.shape[0])
        
        # instantiate gLV fit 
        ode_model = ODE(system = system, 
                    transform = transform,
                    dataframe = df_train, 
                    sys_vars = species, 
                    prior_mean = prior_mean, 
                    alpha=alpha, beta=10.)

        # fit to data 
        ode_model.fit_posterior_EM(n_sample_sgd=1, 
                                   n_sample_hypers=50, 
                                   n_sample_evidence=100, 
                                   patience=3)


        # predict values and save to test dataframe
        x0 = df_test[species].values[0]
        y_preds = ode_model.predict_sample(x0, np.array(df_test.Time.values, float), n_sample=100)
        
        # save predictions 
        df_test.drop(columns='pH', inplace=True)   
        df_test[[f'sample_{i+1}' for i in range(y_preds.shape[0])]] = y_preds[:, :, 0].T
        
        # append to list of dataframes
        df_preds.append(df_test)
        
    # save dataframe
    df_pred = pd.concat(df_preds)
    df_pred.to_csv("kfold/{:}.csv".format(sp.split("_")[0]), index=False)

Computing model evidence...


100%|█████████████████████████████████████████| 100/100 [00:01<00:00, 78.23it/s]


Log evidence: -1115.105
Updating hyperparameters...


100%|██████████████████████████████████████████| 50/50 [00:00<00:00, 123.30it/s]


Updating posterior...
Epoch 1, NEG ELBO: 111.239
Epoch 2, NEG ELBO: 81.397
Epoch 3, NEG ELBO: 77.069
Epoch 4, NEG ELBO: 72.518
Epoch 5, NEG ELBO: 68.165
Epoch 6, NEG ELBO: 65.980
Epoch 7, NEG ELBO: 65.297
Epoch 8, NEG ELBO: 61.362
Epoch 9, NEG ELBO: 59.662
Epoch 10, NEG ELBO: 58.516
set lr to 1.000e-02
Epoch 11, NEG ELBO: 59.724, Slope: -0.031
set lr to 1.000e-02
Epoch 12, NEG ELBO: 58.560, Slope: -0.026
set lr to 1.000e-02
Epoch 13, NEG ELBO: 61.124, Slope: -0.019
set lr to 1.000e-02
Epoch 14, NEG ELBO: 57.243, Slope: -0.015
Epoch 15, NEG ELBO: 60.755, Slope: -0.010
Epoch 16, NEG ELBO: 58.855, Slope: -0.006
Epoch 17, NEG ELBO: 58.563, Slope: -0.002
Epoch 18, NEG ELBO: 58.024, Slope: -0.002
decrease lr to 9.000e-03
Epoch 19, NEG ELBO: 64.770, Slope: 0.004
decrease lr to 8.100e-03
Epoch 20, NEG ELBO: 60.875, Slope: 0.004
decrease lr to 7.290e-03
Epoch 21, NEG ELBO: 57.687, Slope: 0.002
Epoch 22, NEG ELBO: 58.036, Slope: -0.001
Epoch 23, NEG ELBO: 57.606, Slope: -0.001
Epoch 24, NEG ELBO

...

100%|██████████████████████████████████████████| 50/50 [00:00<00:00, 218.51it/s]


Updating posterior...
Epoch 1, NEG ELBO: 78.198
Epoch 2, NEG ELBO: 81.371
Epoch 3, NEG ELBO: 78.395
Epoch 4, NEG ELBO: 80.095
Epoch 5, NEG ELBO: 82.690
Epoch 6, NEG ELBO: 78.716
Epoch 7, NEG ELBO: 82.453
Epoch 8, NEG ELBO: 78.149
Epoch 9, NEG ELBO: 81.816
Epoch 10, NEG ELBO: 80.883
Epoch 11, NEG ELBO: 73.190, Slope: -0.004
decrease lr to 9.000e-03
Epoch 12, NEG ELBO: 88.240, Slope: 0.002
Epoch 13, NEG ELBO: 78.011, Slope: -0.001
decrease lr to 8.100e-03
Epoch 14, NEG ELBO: 88.103, Slope: 0.004
decrease lr to 7.290e-03
Epoch 15, NEG ELBO: 78.595, Slope: 0.003
decrease lr to 6.561e-03
Epoch 16, NEG ELBO: 84.324, Slope: 0.004
Epoch 17, NEG ELBO: 68.675, Slope: -0.003
decrease lr to 5.905e-03
Epoch 18, NEG ELBO: 91.338, Slope: 0.002
decrease lr to 5.314e-03
Epoch 19, NEG ELBO: 78.836, Slope: 0.001
Epoch 20, NEG ELBO: 78.534, Slope: -0.000
Epoch 21, NEG ELBO: 79.197, Slope: -0.007
Epoch 22, NEG ELBO: 81.599, Slope: -0.002
Epoch 23, NEG ELBO: 82.058, Slope: -0.003
decrease lr to 4.783e-03
Ep

100%|████████████████████████████████████████| 100/100 [00:00<00:00, 193.44it/s]

Log evidence: -170.804



/tmp/ipykernel_10370/3494173154.py:46: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[[f'sample_{i+1}' for i in range(y_preds.shape[0])]] = y_preds[:, :, 0].T
/tmp/ipykernel_10370/3494173154.py:46: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_test[[f'sample_{i+1}' for i in range(y_preds.shape[0])]] = y_preds[:, :, 0].T
/tmp/ipykernel_10370/3494173154.py:46: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joinin